<a href="https://colab.research.google.com/github/prushton2/977Z/blob/master/RoboticsScoreProgram.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Mount Google Drive


In [0]:
from google.colab import drive
drive.mount('/content/drive', force_remount=False)

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


# Class definitions

## Json manager class

In [0]:
import matplotlib.pyplot as plt
import csv
import json
from termcolor import colored, cprint 
import time 

null = None #I can't be bothered to remember null is None in python
true = True
false = False


class JsonManager:
  def __init__(self, path, fType): # fType should be 'score', 'comp', or 'team' depending on which json file is being opened
    self.path = path
    self.fType = fType
  def load(self):
    #opens json file and returns data
    with open(self.path, mode="r") as theFile:
      return json.load(theFile) 
      
  def save(self, data):
    #opens json file and saves data
    with open(self.path, mode="w") as theFile:
      json.dump(data, theFile)

  def addData(self, key, value, function): #Adds data to a json key, but abstracted. 
    jsonFile = self.load()#JsonManager.open()

    if(function == 'set'):
      exec("jsonFile"+str(key)+" = "+str(value))
    elif(function == 'append'):
      exec("jsonFile"+str(key)+".append("+str(value)+")")
    else:
      raise ValueError("The function parameter must be 'set' or 'append', not", function)
    self.save(jsonFile)

  

## Competition Manager

In [0]:
class Comp: #This is used as a datatype to hold the data for a competition
  def __init__(self, id, name, date, path):
    self.id = id;
    self.name = name;
    self.date = date;
    self.path = path;

class AllComps:
  def __init__(self, compList):
    self.compList = compList;
  def getCompFromId(self, id):
    for i in self.compList:
      if(i.id == id):
        return i

## Compiler

In [0]:
class Compiler:
  def __init__(self, comps):
    self.comps = comps;

  def setCompIDs(self, comps):
    self.comps = comps
  
  def compileComps(self): # Will compile the csv data into the jsons.
    for thisComp in self.comps:
      compFile.addData('['+str(thisComp.id)+']', {"Matches":[],"Skills":[]}, 'set')

      with open(thisComp.path, mode='r') as thisFile:
        reader = csv.DictReader(thisFile)
        line_count=0
        for row in reader:
          print("Adding match", row["Match"], "of comp", thisComp.name)
          if(int(row["Red Score"]) > int(row["Blue Score"])):
            winner = 'Red'
          elif(int(row["Blue Score"]) > int(row["Red Score"])):
            winner = 'Blue'
          else:
            winner = null
          thisMatch = [
            row["Match"],
            thisComp.id, 
            [int(row["Red Score"]), int(row["Blue Score"])],
            [row["Red Team (1)"], row["Red Team (2)"]], 
            [row["Blue Team (1)"], row["Blue Team (2)"]],
            winner
          ]

          compFile.addData('["'+str(thisComp.id)+'"]["Matches"]', thisMatch, 'append')
  
  def compileTeams(self):
    json = compFile.load()
    for i in json:
      for j in json[i]["Matches"]:
        for k in j[3]:
          try:
            teamFile.addData("['"+k+"']['Matches']", j, 'append')
            print("Added", j, "to team", k)
          except:
            teamFile.addData("['"+k+"']", {"Matches":[j],"Skills":[]}, 'set')
            print("Created team", k, "with match", j)
        for k in j[4]:
          try:
            teamFile.addData("['"+k+"']['Matches']", j, 'append')
            print("Added", j, "to team", k)
          except:
            teamFile.addData("['"+k+"']", {"Matches":[j],"Skills":[]}, 'set')
            print("Created team", k, "with match", j)

  def compileScores(self):
    scores = scoreFile.load();
    teams = teamFile.load();
    for team in teams:
      scoreFile.addData("['"+team+"']", [0], 'set')
      print("Created a record for team", team, "with 0 points")
      for match in teams[team]["Matches"]:
        scores = scoreFile.load();
        if(match[5] == 'Red'): #Create the number to add/subtract to the players score
          delta =  (int(match[2][0]) / (int(match[2][0]) + int(match[2][1])))*100
        if(match[5] == 'Blue'):
          delta =  (int(match[2][1]) / (int(match[2][0]) + int(match[2][1])))*100
        if(match[5] == null):
          delta = 0
        
        if(not(MatchHandler.hasWon(team, match))):
          delta *= -1;

        # print(team)
        z = (scores[team][len(scores[team])-1] + delta)
        scoreFile.addData('["'+team+'"]', z, 'append')
        print("Added", delta, "points to the record for team", team)

          
        


## Match Handler

In [0]:
class MatchHandler:
  @staticmethod
      
  def getColor(team, match):
    if(team == match[3][0] or team == match[3][1]):
      return "Red"
    if(team == match[4][0] or team == match[4][1]):
      return "Blue"

  def hasWon(team, match):
    if(MatchHandler.getColor(team, match) == match[5]):
      return True
    else:
      return False # set cube stack

## Team Class

In [0]:
class Team:
  def __init__(self, teamName):
    self.team = teamName;

  def hasCategory(self, category, categories):
    return category in categories or "all" == categories

  def showStats(self, categories):
    if(self.hasCategory("matches", categories)):
      teams = teamFile.load();
      for i in teams[self.team]["Matches"]:
        print(allComps.getCompFromId(i[1]).name, "on", allComps.getCompFromId(i[1]).date, "   |   ", end="")
        
        if(MatchHandler.hasWon(self.team, i)):
          color='green'
        elif(i[5] == null):
          color='grey'
        else:
          color='red'
        
        print(colored(i[0], color, attrs=['reverse', 'blink']), end='')
        print("  |  ", end='')

        if(i[5] == null):
          print(colored(i[3][0]+", "+i[3][1]+" : "+str(i[2][0])+" vs "+str(i[2][1])+" : "+i[4][0]+", "+i[4][1], 'grey'), end='')

        if(i[5] == 'Red'):
          print(colored(i[3][0]+", "+i[3][1]+" : "+str(i[2][0])+" vs ", 'red'), end='')
          print(str(i[2][1])+" : "+i[4][0]+", "+i[4][1], end='')

        if(i[5] == 'Blue'):
          print(i[3][0]+", "+i[3][1]+" : "+str(i[2][0]), end='')
          print(colored(" vs "+str(i[2][1])+" : "+i[4][0]+", "+i[4][1], 'blue'), end='')

        print("")

    if(self.hasCategory("scorePlot", categories)):
      scores = scoreFile.load()
      mplCreator.newPlot(false, scores[self.team], 'Scores')

    if(self.hasCategory("score", categories)):
      scores = scoreFile.load()
      print(scores[self.team][len(scores[self.team])-1])      
    
        
        
          

## Matplotlib Creators

In [0]:
class mplCreator:
  @staticmethod
  def getArrayOfLength(length):
    array = []
    for i in range(length):
      array.append(i)
    return array

  def newPlot(xArray, yArray, title):
    fig, ax = plt.subplots()
    #Create a plot instance
    
    #make it dark
    # https://matplotlib.org/3.1.1/tutorials/introductory/customizing.html
    plt.rcParams.update({
        "lines.color": "white",
        "patch.edgecolor": "white",
        "text.color": "black",
        "axes.facecolor": "black",
        "axes.edgecolor": "lightgray",
        "axes.labelcolor": "white",
        "xtick.color": "white",
        "ytick.color": "white",
        "grid.color": "lightgray",
        "figure.facecolor": "black",
        "figure.edgecolor": "black",
        "savefig.facecolor": "black",
        "savefig.edgecolor": "black"})
    #Place points on the graph
    if(xArray == False and yArray == False):
      print("We need a list, not 2 booleans")
    if(xArray == False):
      xArray = mplCreator.getArrayOfLength(len(yArray))
    if(yArray == False):
      yArray = mplCreator.getArrayOfLength(len(xArray))

    for i in range(len(yArray)):#Color in the lines fron point to point based on gain or loss
      try:
        if(yArray[i] > yArray[i+1]):
          ax.plot([xArray[i], xArray[i+1]], [yArray[i], yArray[i+1]], color='r')
        elif(yArray[i] < yArray[i+1]):
          ax.plot([xArray[i], xArray[i+1]], [yArray[i], yArray[i+1]], color='g')
        else:
          ax.plot([xArray[i], xArray[i+1]], [yArray[i], yArray[i+1]], color='b')
      except:
        print("")
    ax.scatter(xArray, yArray)
    #Set the title
    ax.set_title(title)
    #Show the plot
    fig.show()

## Score Class

In [0]:
class Score:
  def __init__(self):
    self.Ranks = []
  

  def rankTeams(self):
    IMM_scores = scoreFile.load()
    self.Ranks = []
    self.teams = []

    for i in IMM_scores:
      self.teams.append(i)
    print(self.teams)


    for team in IMM_scores:
      teamScore = IMM_scores[team][-1]
      rankFound = false
      print(team)

      for i in range(len(self.Ranks)):
        print(self.Ranks[i], ":", IMM_scores[self.Ranks[i]][-1], "||", end='')


      if(self.Ranks == []):
        self.Ranks = [team]
        print("--- Initialized ranks with team", team)
      else:
        i=-1
        while(not(rankFound)):
          i += 1
          print("--- Index:", i)
          try:
            comparisonScore = IMM_scores[self.Ranks[i]][-1]
            print("--- Comparison: Team:", self.Ranks[i], "Score:", comparisonScore)
            print("--- This: Team:", team, "Score:", teamScore)

            if(teamScore > comparisonScore):
              print("---", teamScore, ">", comparisonScore)
              print("--- found a spot for", team, "at place", i)
              rankFound = true
              self.Ranks.insert(i-1, team)
            else:
              print("---", teamScore, "<", comparisonScore)
          except:
            rankFound = true
            self.Ranks.append(team)
            print("--- Hit list limit at", i, "appending", team, "to ranks list")
            i=-1



    for i in range(len(self.teams)):
      print(str(i+1), self.teams[i], IMM_scores[self.teams[i]][-1])

# Instantiations

In [0]:
localpath = "/content/drive/My Drive/RoboticsScoreProgram/Competitions"
compList = [
            Comp(0.0,  "Hartford",                        "10/19/19", localpath+"/VRC_10_19_19_Hartford.csv"),
            Comp(1.0,  "Quinsigamond Community College",  "11/02/19", localpath+"/VRC_11_02_19_Madison.csv"),
            Comp(2.0,  "Madison",                         "11/02/19", localpath+"/VRC_11_02_19_QCC.csv"),
            Comp(3.0,  "Framingham",                      "11/09/19", localpath+"/VRC_11_09_19_Framingham.csv"),
            Comp(4.0,  "Danbury",                         "11/16/19", localpath+"/VRC_11_16_19_Monroe.csv"),
            Comp(5.0,  "North Andover",                   "11/23/19", localpath+"/VRC_11_23_19_NorthAndover.csv"),
            Comp(6.0,  "Hopkinton",                       "12/07/19", localpath+"/VRC_12_07_19_Hopkinton.csv"),
            Comp(7.0,  "CTEEA Masuk",                     "12/07/19", localpath+"/VRC_12_07_19_Masuk.csv"),
            Comp(8.0,  "Quinsigamond Community College",  "12/21/19", localpath+"/VRC_12_21_19_QCC.csv"),
            Comp(9.0,  "CTEEA Bolton CT",                 "01/04/20", localpath+"/VRC_01_04_20_CTEEABolton.csv"),
            Comp(10.0, "Quinsigamond Community College",  "01/04/20", localpath+"/VRC_01_04_20_QCC.csv"),
            Comp(11.0, "CTEEA Middleton",                 "01/11/20", localpath+"/VRC_01_11_20_CTEEAMiddleton.csv"),
            Comp(12.0, "Wave at WPI",                     "01/16/20", localpath+"/VRC_01_16_20_Wave.csv"),
            Comp(13.0, "Hopkinton",                       "01/19/20", localpath+"/VRC_01_19_20_Hopkinton.csv")

]
# print(compList[-1])

allComps = AllComps(compList)
compiler = Compiler(compList)

compFile = JsonManager("/content/drive/My Drive/RoboticsScoreProgram/Json/Comps.json", 'comp')
teamFile = JsonManager("/content/drive/My Drive/RoboticsScoreProgram/Json/Teams.json", 'team')
scoreFile = JsonManager("/content/drive/My Drive/RoboticsScoreProgram/Json/Scores.json", 'score')

# Compiling
Compiles the CSV files into the JSON files

In [0]:
if(false): #This compiles the CSV files to the JSON files. Do not run unless you have made changes to the CSV files or the compiler code
  startTime = time.time()
  compFile.save({})
  teamFile.save({})
  scoreFile.save({})

  compiler.compileComps()
  compiler.compileTeams()
  compiler.compileScores()
  print("Operation took", time.time()-startTime,"seconds")


# Debug

In [0]:
IMM_scores = scoreFile.load()
teams = ['977Z']
IMM_scores[teams[0]
           ][-1]

1258.2226352308212

In [86]:
s1 = Score();
s1.rankTeams();
print(s1.Ranks)

['1898A', '4478Z', '5150H', '4478D', '8079R', '1695C', '8079M', '5150G', '4478A', '8878A', '8878C', '1898R', '5150D', '8878E', '8878F', '8878D', '8370A', '5150J', '1898M', '5150F', '8878B', '1697B', '8878G', '4478V', '1697A', '8079A', '4478B', '18891A', '1695B', '8079C', '4478F', '18891B', '4478C', '5150E', '4478R', '1695A', '1188A', '1695E', '195D', '9909A', '195E', '195C', '1695D', '9909C', '195B', '375X', '1188B', '9909B', '195A', '169Y', '3379A', '49585B', '4344Z', '9421X', '4898A', '2606B', '1898S', '4344Y', '817F', '2442B', '4344X', '4898C', '817D', '4344A', '3157A', '4898B', '64345A', '817B', '2606C', '2606A', '4811A', '10102X', '2602H', '4716A', '48425A', '63857E', '2442A', '9228A', '9228B', '1127Z', '785Z', '2713A', '2442F', '2713B', '9421V', '9228C', '9421R', '785E', '785A', '4716D', '10102A', '2442E', '977Z', '63857A', '63857D', '785B', '2713C', '902B', '39545B', '1618A', '50239A', '17814V', '902E', '17814A', '50239B', '17814E', '39545A', '17814Y', '902X', '9909F', '17814B',

In [0]:
# IMM_scores = scoreFile.load()
# print(IMM_scores[0]) 

# Show a team's scores

In [0]:
a977Z = Team("977Z")
a977Z.showStats("all")

# Structure
* Json Files
  * Competitions:
    * Holds every played match sorted by competition then time
  * Scores
    * Holds every team's score, and their score over time stored in a list
  * Teams
    * Stores every team, and every match they have played.

# Backlog

### Complete
* Create Json manager class
* Create competition class
* Create competition ID system
* Read and compile csvs into jsons
  * Have a json for comps and a json for teams
* Create scoring system

### In progress
* Print a teams stats nicely
* Show scores over time

### TODO

# Sprint Task List

#### Complete

#### In progress
* Iterate through team matches and print nicely
* Create class to hold team name

#### TODO

# Json format:

## Comps:
    {
      "CompName":{
        "Matches":[
          [
            "matchName",
            compId,
            [redScore, blueScore],
            [red1, red2],
            [blue1, blue2],
            "winner"
          ]
        ],
        "Skills": [
          [
            "TeamName",
            [autonScore, driverScore]
          ]
        ]
      }
    }
## Scores:

    {
      "teamNumber": [
        score1,
        score2,
        score3...
      ]
    }

## Teams:

    {
      "teamNumber": {
        "Matches: [
          "referenceToCompsJsonMatchIndex",
        ],
        "Skills": [

        ]
      }
    }


